## MOEA/D -TFG- Análisis Multiobjetivo de Selección Óptima de Pozos de Monitoreo de Agua Subterránea

#### LIBRERÍAS UTILIZADAS

In [ ]:
import os
import time
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from scipy.spatial.distance import cdist
from pymoo.core.problem import Problem
from pymoo.algorithms.moo.moead import MOEAD
from pymoo.operators.crossover.hux import HUX
from pymoo.operators.mutation.bitflip import BitflipMutation
from pymoo.optimize import minimize
from pymoo.util.ref_dirs import get_reference_directions
from pymoo.core.sampling import Sampling
from pymoo.core.repair import Repair
from pymoo.indicators.hv import HV
from pymoo.indicators.gd import GD
from pymoo.indicators.igd import IGD
from pymoo.decomposition.tchebicheff import Tchebicheff
from pandas.plotting import parallel_coordinates
import secrets
from math import comb
from scipy.spatial import cKDTree
from pymoo.util.nds.non_dominated_sorting import NonDominatedSorting
from pymoo.core.callback import Callback

#### PARÁMETROS GLOBALES

In [ ]:
k_values = [10, 20, 30, 40, 50, 60, 70, 80, 90, 100]

# Probabilidades y configuración
p_cross = 0.95
p_mut = 0.05
obj = 3
n_partitions = 13
final_gen = 2000
save_gens = [100, 500, 1000, 1500, 2000]

# Directorio raíz de salida
OUTPUT_ROOT = os.path.join("OUTPUT", "Resultados_MOEAD")

#### CARGA DE DATOS

In [ ]:
df = pd.read_csv('Pozos_GA_datos_entrada_revisado.csv', delimiter=';', encoding='Latin-1')
# normalizaciones / conversiones
df['WQI'] = df['WQI'].str.replace(',', '.', regex=False).astype(float)
df['ivct'] = df['ivct'].str.replace(',', '.', regex=False).astype(float)
df['ivnt'] = df['ivnt'].str.replace(',', '.', regex=False).astype(float)
df['x'] = df['x'].astype(int)
df['y'] = df['y'].astype(int)
df['prof__m_'] = df['prof__m_'].astype(int)

x_coords = df['x'].values
y_coords = df['y'].values
WQI = df['WQI'].values
prioridad = df['Prioridad'].values
n_b = len(WQI)

In [ ]:
# Grid para IDW/interpolaciones
m_x = 50
m_y = 50
grid_nash = m_x
grid_entropia = m_x
grid_x, grid_y = np.meshgrid(
    np.linspace(min(x_coords), max(x_coords), m_x),
    np.linspace(min(y_coords), max(y_coords), m_y)
)

#### FUNCIÓN DE SELECCIÓN DE MEJORES SOLUCIONES

In [ ]:
def select_best_solution(pareto_front):
    """
    Selecciona el índice de la mejor solución del frente de Pareto basándose
    en la suma de los objetivos normalizados (0-1).

    Los objetivos son invertidos (1 - norm_F) porque son maximizados
    en el problema (NSE, Prioridad, Entropía), pero PyMOO los minimiza
    como negativos.

    Args:
        pareto_front (np.ndarray): Array 2D con los valores de los objetivos
                                   (negativos) de las soluciones en el frente de Pareto.
                                   Forma (num_soluciones, num_objetivos).

    Returns:
        int: El índice de la solución considerada la "mejor" dentro del frente de Pareto.
    """
    # Normalización min-max (invertida porque son objetivos a minimizar)
    # Se aplica 1 - norm_F porque NSE, Prioridad y Entropia son objetivos a maximizar
    # pero se definieron como negativos en el problema para que PyMOO los minimice.
    
    # Manejar el caso de división por cero si min == max
    norm_F = np.zeros_like(pareto_front, dtype=float)
    for i in range(pareto_front.shape[1]):
        col_min = np.min(pareto_front[:, i])
        col_max = np.max(pareto_front[:, i])
        if col_max - col_min > 1e-10: # Para evitar división por cero
            norm_F[:, i] = (pareto_front[:, i] - col_min) / (col_max - col_min)
        else:
            norm_F[:, i] = 0.5 # Asignar un valor neutral si todos son iguales

    norm_F = 1 - norm_F  # Convertir a maximización (ya que los originales son a maximizar, pero se minimizan sus negativos)
  
    # Calcular la suma de los scores normalizados
    scores = np.sum(norm_F, axis=1)
    # El índice de la solución con el score más alto es la "mejor"
    best_idx = np.argmax(scores)
    return best_idx

#### DEFINICIÓN DE LA FUNCIÓN DE INTERPOLACIÓN

In [ ]:
def idw_interpolation(selected_wells):
    indices = np.where(selected_wells == 1)[0]
    if len(indices) == 0:
        return np.zeros((grid_nash, grid_nash))
    active_x, active_y = x_coords[indices], y_coords[indices]
    active_WQI = WQI[indices]
    grid_points = np.c_[grid_x.ravel(), grid_y.ravel()]
    well_points = np.c_[active_x, active_y]
    distances = cdist(grid_points, well_points)
    weights = 1 / (distances ** 2 + 1e-10)
    interpolated = np.sum(weights * active_WQI, axis=1) / np.sum(weights, axis=1)
    return interpolated.reshape(grid_nash, grid_nash)

WQI_star_grid = idw_interpolation(np.ones(n_b))
WQI_star_mean = np.mean(WQI_star_grid)

#### CARGA DE LOS FRENTES IDEALES

In [ ]:
def load_pareto_front(seed, k, gen, obj=3):
    """
    Carga el frente ideal desde MOEAD/semilla{seed}/true_pareto_K{k}_GN{gen}.npy
    Devuelve np.ndarray (N x obj) en espacio de minimización (valores negativos).
    
    IMPORTANTE: El archivo NPY ya contiene valores NEGATIVOS (espacio de minimización).
    Esta función los retorna directamente sin modificarlos.
    """
    path = os.path.join("MOEAD", f"semilla{seed}", f"true_pareto_K{k}_GN{gen}.npy")

    if not os.path.exists(path):
        return None

    try:
        arr = np.load(path)

        
        # Validar que tenga el número correcto de columnas
        if arr.ndim != 2 or arr.shape[1] != obj:
            return None
        return arr

    except Exception as e:
        return None

#### DEFINICIÓN DEL PROBLEMA PARA LA SELECCIÓN DE POZOS

In [ ]:
class WellSelectionProblem(Problem):
    def __init__(self, k):
        super().__init__(n_var=n_b, n_obj=3, xl=0, xu=1, type_var=bool)
        self.k = k

    def _evaluate(self, x, out, *args, **kwargs):
        f1_list, f2_list, f3_list = [], [], []
        for row in x:
            interpolated = idw_interpolation(row)
            # map para pozos
            x_idx = np.clip(np.round((x_coords - min(x_coords)) / (max(x_coords) - min(x_coords)) * (grid_nash - 1)).astype(int), 0, grid_nash - 1)
            y_idx = np.clip(np.round((y_coords - min(y_coords)) / (max(y_coords) - min(y_coords)) * (grid_nash - 1)).astype(int), 0, grid_nash - 1)
            predicted = interpolated[y_idx, x_idx]

            num = np.sum((interpolated - WQI_star_grid) ** 2)
            den = np.sum((WQI_star_grid - WQI_star_mean) ** 2)
            nse = 1 - num / den if den != 0 else -np.inf

            selected = np.where(row == 1)[0]
            prioridad_val = np.sum(prioridad[selected])/self.k if self.k>0 else 0.0

            if len(selected) == 0:
                entropy = 0.0
            else:
                grid_size_x, grid_size_y = grid_entropia, grid_entropia
                bins_x = np.linspace(x_coords.min(), x_coords.max(), grid_size_x + 1)
                bins_y = np.linspace(y_coords.min(), y_coords.max(), grid_size_y + 1)
                counts, _, _ = np.histogram2d(x_coords[selected], y_coords[selected], bins=[bins_x, bins_y])
                total = np.sum(counts)
                if total > 0:
                    probs = counts.ravel() / total
                    probs = probs[probs > 0]
                    H = -np.sum(probs * np.log(probs))
                    H_max = np.log(grid_size_x * grid_size_y) if (grid_size_x * grid_size_y) > 0 else 1.0
                    entropy = H / H_max if H_max > 0 else 0.0
                else:
                    entropy = 0.0

            # Negamos para maximizar (pymoo minimiza por defecto)
            f1_list.append(-nse)
            f2_list.append(-prioridad_val)
            f3_list.append(-entropy)

        out["F"] = np.column_stack([f1_list, f2_list, f3_list])

#### MUESTREO DE LA POBLACIÓN + REPARACIÓN

In [ ]:
class FixedKSampling(Sampling):
    def __init__(self, valid_indices, rng, k):
        super().__init__()
        self.valid_indices = valid_indices
        self.rng = rng
        self.k = k

    def _do(self, problem, n_samples, **kwargs):
        X = np.zeros((n_samples, problem.n_var), dtype=bool)
        for i in range(n_samples):
            selected = self.rng.choice(self.valid_indices, size=self.k, replace=False)
            X[i, selected] = True
        return X

class WellRepair(Repair):
    def __init__(self, target_wells, valid_indices, rng):
        super().__init__()
        self.target_wells = target_wells
        self.valid_indices = np.array(valid_indices)
        self.rng = rng

    def _do(self, problem, X, **kwargs):
        X_repaired = X.copy()
        for i in range(len(X_repaired)):
            current = int(np.sum(X_repaired[i]))
            if current > self.target_wells:
                idx = np.where(X_repaired[i])[0]
                to_remove = self.rng.choice(idx, current - self.target_wells, replace=False)
                X_repaired[i, to_remove] = False
            elif current < self.target_wells:
                idx = list(set(np.where(~X_repaired[i])[0]) & set(self.valid_indices))
                if len(idx) >= (self.target_wells - current):
                    to_add = self.rng.choice(idx, self.target_wells - current, replace=False)
                    X_repaired[i, to_add] = True
                else:
                    to_add = self.rng.choice(idx, min(len(idx), self.target_wells - current), replace=False) if len(idx)>0 else []
                    if len(to_add)>0:
                        X_repaired[i, to_add] = True
        return X_repaired

#### CALLBACK

In [ ]:
class SaveCallback(Callback):
    def __init__(self, save_gens, out_dir, k, df, m_x, p_cross, p_mut, seed, obj, n_partitions, true_pareto):
        super().__init__()
        self.save_gens = set(save_gens)
        self.out_dir = out_dir
        self.k = k
        self.df = df
        self.m_x = m_x
        self.p_cross = p_cross
        self.p_mut = p_mut
        self.seed = seed
        self.obj = obj
        self.n_partitions = n_partitions
        self.true_pareto = true_pareto
        self.history_metrics = []
        self.start_time = time.time()

    def notify(self, algorithm):
        current_gen = algorithm.n_gen
        if current_gen in self.save_gens:
            execution_time = time.time() - self.start_time
            print(f"Guardando resultados en generación {current_gen} (K={self.k})")
            output_result(
                algorithm.result(),
                gen=current_gen,
                k=self.k,
                out_dir=self.out_dir,
                df=self.df,
                m_x=self.m_x,
                p_cross=self.p_cross,
                p_mut=self.p_mut,
                seed=self.seed,
                obj=self.obj,
                n_partitions=self.n_partitions,
                true_pareto=self.true_pareto,
                history_metrics=self.history_metrics,
                execution_time=execution_time
            )

#### OUTPUT

In [ ]:
def output_result(res, gen, k, out_dir, df, m_x, p_cross, p_mut, seed, obj, n_partitions, true_pareto=None, history_metrics=None, execution_time=None):
    pareto_front = res.F
    selected_solutions = res.X

    ref_point = [0.0, 0.0, 0.0]
    hv = HV(ref_point=ref_point)
    try:
        hv_value = float(hv(pareto_front))
    except Exception:
        hv_value = float('nan')
    print(f"Hipervolumen (HV) K={k}, Gen={gen}: {hv_value}")

    gd_value = np.nan
    igd_value = np.nan
    if true_pareto is not None:
        try:     
            pareto_front_positive = -pareto_front
            true_pareto_positive = -true_pareto
            
            # Calcular GD e IGD con valores positivos
            gd_indicator = GD(true_pareto_positive)
            igd_indicator = IGD(true_pareto_positive)
            gd_value = float(gd_indicator(pareto_front_positive))
            igd_value = float(igd_indicator(pareto_front_positive))

        except Exception as e:
            import traceback
            traceback.print_exc()
            gd_value = np.nan
            igd_value = np.nan
    else:
        print("No se proporcionó frente de referencia. GD/IGD = NaN")

    # DataFrame con resultados (valores positivos para visualización)
    df_results = pd.DataFrame({
        'NSE': -pareto_front[:, 0],
        'Prioridad': -pareto_front[:, 1],
        'Entropia': -pareto_front[:, 2],
        'Pozos': np.sum(selected_solutions, axis=1)
    })

    # carpeta específica K y gen
    current_gen_folder = os.path.join(out_dir, f"K{k}", f"GN{gen}")
    os.makedirs(current_gen_folder, exist_ok=True)

    # seleccionar mejor solución
    best_idx = select_best_solution(pareto_front)
    best_solution = selected_solutions[best_idx].astype(bool)
    best_nse = -pareto_front[best_idx, 0]
    best_prioridad = -pareto_front[best_idx, 1]
    best_entropia = -pareto_front[best_idx, 2]

    df_best = df[best_solution].copy()
    n_pozos_best = df_best.shape[0]

    # conversión para CSV
    df_best_export = df_best.copy()
    df_best_export['WQI'] = df_best_export['WQI'].astype(str).str.replace('.', ',', regex=False)
    df_best_export['ivct'] = df_best_export['ivct'].astype(str).str.replace('.', ',', regex=False)
    df_best_export['ivnt'] = df_best_export['ivnt'].astype(str).str.replace('.', ',', regex=False)
    for col in ['x','y','prof__m_','Prioridad']:
        if col in df_best_export.columns:
            df_best_export[col] = df_best_export[col].astype(str)

    timestamp = time.strftime("%d-%m-%Y_%H-%M-%S", time.localtime())

    best_file_path = os.path.join(current_gen_folder, f"MEJOR_SOL_NP{n_pozos_best}_{timestamp}.csv")
    df_best_export.to_csv(best_file_path, index=False, sep=";", encoding='UTF-8')

    # guardar cada solución del frente
    for i, sol in enumerate(selected_solutions, start=1):
        df_pozos = df[sol.astype(bool)].copy()
        df_pozos_export = df_pozos.copy()
        df_pozos_export['WQI'] = df_pozos_export['WQI'].astype(str).str.replace('.', ',', regex=False)
        df_pozos_export['ivct'] = df_pozos_export['ivct'].astype(str).str.replace('.', ',', regex=False)
        df_pozos_export['ivnt'] = df_pozos_export['ivnt'].astype(str).str.replace('.', ',', regex=False)
        for col in ['x','y','prof__m_','Prioridad']:
            if col in df_pozos_export.columns:
                df_pozos_export[col] = df_pozos_export[col].astype(str)
        file_path = os.path.join(current_gen_folder, f"SOL{i}_NP{df_pozos.shape[0]}_{timestamp}.csv")
        df_pozos_export.to_csv(file_path, index=False, sep=";", encoding='UTF-8')

    # guardar resultados de frente y soluciones
    np.save(os.path.join(current_gen_folder, f"pareto_F_K{k}_GN{gen}.npy"), pareto_front)
    np.save(os.path.join(current_gen_folder, f"pareto_X_K{k}_GN{gen}.npy"), selected_solutions)
    df_results.to_csv(os.path.join(current_gen_folder, f"resultados_pareto_{timestamp}.csv"), index=False, sep=";", encoding='UTF-8')

    # guardar resumen y metricas
    poblacion = comb(obj + n_partitions - 1, n_partitions)
    metrics = {
        'k': k,
        'gen': gen,
        'HV': hv_value,
        'GD': gd_value,
        'IGD': igd_value,
        'N_puntos_pareto': pareto_front.shape[0],
        'Tiempo_seg': execution_time if execution_time is not None else np.nan
    }
    if history_metrics is not None:
        history_metrics.append(metrics)

    resumen_txt = os.path.join(current_gen_folder, f"parametros_{timestamp}.txt")
    with open(resumen_txt, 'w', encoding='utf-8') as f:
        f.write(f"Seed: {seed}\n")
        f.write(f"K: {k}\n")
        f.write(f"Generacion: {gen}\n")
        f.write(f"HV: {hv_value}\n")
        f.write(f"GD: {gd_value}\n")
        f.write(f"IGD: {igd_value}\n")
        f.write(f"Tiempo_seg: {metrics['Tiempo_seg']}\n")
        f.write(f"Poblacion_estimada: {poblacion}\n")
        f.write(f"\nMejor solución:\n")
        f.write(f"- Índice: {best_idx}\n")
        f.write(f"- NSE: {best_nse:.4f}\n")
        f.write(f"- Prioridad: {best_prioridad:.4f}\n")
        f.write(f"- Entropía: {best_entropia:.4f}\n")
        f.write(f"- Pozos seleccionados: {n_pozos_best}\n")

    # Graficos compactos
    try:
        fig, axs = plt.subplots(2, 2, figsize=(12, 9))
        
        axs[0,0].scatter(df_results['Prioridad'], df_results['NSE'], c='b', alpha=0.6)
        axs[0,0].set_xlabel("Proporción de pozos prioritarios")
        axs[0,0].set_ylabel("NSE")
        axs[0,0].set_title("NSE vs Prioridad")
        axs[0,0].grid(True, alpha=0.3)

        axs[0,1].scatter(df_results['Entropia'], df_results['NSE'], c='green', alpha=0.6)
        axs[0,1].set_xlabel("Entropía Espacial")
        axs[0,1].set_ylabel("NSE")
        axs[0,1].set_title("NSE vs Entropía")
        axs[0,1].grid(True, alpha=0.3)

        axs[1,0].scatter(df_results['Entropia'], df_results['Prioridad'], c='purple', alpha=0.6)
        axs[1,0].set_xlabel("Entropía Espacial")
        axs[1,0].set_ylabel("Proporción de pozos prioritarios")
        axs[1,0].set_title("Prioridad vs Entropía")
        axs[1,0].grid(True, alpha=0.3)

        # Coordenadas paralelas
        df_parallel = df_results[['NSE','Prioridad','Entropia']].copy()
        df_parallel['Solución'] = 'Frontera'
        best_parallel = pd.DataFrame({
            'NSE':[best_nse],
            'Prioridad':[best_prioridad],
            'Entropia':[best_entropia],
            'Solución':['Mejor']
        })
        df_parallel = pd.concat([df_parallel, best_parallel], ignore_index=True)
        
        # Normalización Min-Max
        for col in ['NSE','Prioridad','Entropia']:
            min_val = df_parallel[col].min()
            max_val = df_parallel[col].max()
            if max_val > min_val:
                df_parallel[col] = (df_parallel[col] - min_val)/(max_val - min_val)
            else:
                df_parallel[col] = 0.5
        
        parallel_coordinates(
            df_parallel, 
            class_column='Solución', 
            cols=['NSE','Prioridad','Entropia'], 
            ax=axs[1,1], 
            colormap='viridis',
            alpha=0.7
        )
        axs[1,1].set_title("Coordenadas Paralelas (Normalizadas)")
        axs[1,1].set_ylabel("Valores Normalizados")
        axs[1,1].grid(True, alpha=0.3)
        
        plt.suptitle(f"Frente de Pareto - K={k}, Gen={gen}\nGD={gd_value:.6f}, IGD={igd_value:.6f}", fontsize=14)
        plt.tight_layout()
        plt.savefig(os.path.join(current_gen_folder, f"frente_combinado_{timestamp}.png"), dpi=200)
        plt.close(fig)
    except Exception as e:
        print("Warning: error generando graficos:", e)


#### EJECUCIÓN PRINCIPAL

In [ ]:
def ejecutar_todas_las_semillas():
    os.makedirs(OUTPUT_ROOT, exist_ok=True)
    termination = ('n_gen', final_gen)

    poblacion = int(comb(obj + n_partitions - 1, n_partitions))
    print(f"Población estimada (combinatoria): {poblacion}")

    all_history_global = []

    # Lista de semillas reales
    seeds = [1827841104, 3893035886, 2761146642, 1589321152, 3139764589]

    # Bucle principal: recorrer las 5 semillas
    for seed_index, seed in enumerate(seeds, start=1):
        print(f"\n{'='*60}")
        print(f"=== Semilla {seed_index}: {seed} ===")
        print(f"{'='*60}")
        
        rng = np.random.default_rng(seed)
        np.random.seed(seed)

        seed_folder = os.path.join(OUTPUT_ROOT, f"seed{seed_index}")
        os.makedirs(seed_folder, exist_ok=True)

        # Ejecutar para cada valor de K
        for k in k_values:
            print(f"\n{'-'*60}")
            print(f"--- Ejecutando K={k} (semilla {seed_index} → {seed}) ---")
            print(f"{'-'*60}")

            k_dir = os.path.join(seed_folder, f"K{k}")
            os.makedirs(k_dir, exist_ok=True)

            true_pareto = load_pareto_front(seed_index, k, gen=2000, obj=obj)

            valid_indices = np.arange(n_b)
            problem = WellSelectionProblem(k)

            ref_dirs = get_reference_directions("uniform", obj, n_partitions=n_partitions)
            algorithm = MOEAD(
                ref_dirs=ref_dirs,
                n_neighbors=15,
                prob_neighbor_mating=0.9,
                sampling=FixedKSampling(valid_indices, rng, k=k),
                decomposition=Tchebicheff(),
                crossover=HUX(prob=p_cross),
                mutation=BitflipMutation(prob=p_mut),
                repair=WellRepair(k, valid_indices, rng)
            )

            cb = SaveCallback(
                save_gens=save_gens, out_dir=k_dir, k=k,
                df=df, m_x=m_x, p_cross=p_cross, p_mut=p_mut,
                seed=seed, obj=obj, n_partitions=n_partitions,
                true_pareto=true_pareto
            )

            start = time.time()
            res = minimize(problem, algorithm, termination, seed=seed, verbose=True, callback=cb)
            elapsed = time.time() - start
            
            print(f"\n Terminó K={k} (semilla {seed_index}) en {elapsed:.2f} seg ({elapsed/60:.2f} min)")

            hist = cb.history_metrics if hasattr(cb, 'history_metrics') else []
            all_history_global.extend(hist)

            output_result(
                res, gen=final_gen, k=k, out_dir=k_dir, df=df, m_x=m_x,
                p_cross=p_cross, p_mut=p_mut, seed=seed, obj=obj,
                n_partitions=n_partitions, true_pareto=true_pareto,
                history_metrics=hist, execution_time=elapsed
            )

            # Guardar csv por K
            try:
                df_hist = pd.DataFrame(hist)
                if not df_hist.empty:
                    df_hist.to_csv(
                        os.path.join(k_dir, f"metrics_history_seed{seed_index}_K{k}.csv"),
                        index=False, sep=';', encoding='utf-8'
                    )
            except Exception as e:
                print("Error guardando history csv:", e)

        # Al terminar la semilla, guardar resumen global
        try:
            seed_history = [m for m in all_history_global if m.get('k') in k_values]
            if len(seed_history) > 0:
                df_seed = pd.DataFrame(seed_history)
                df_seed.to_csv(
                    os.path.join(seed_folder, f"metrics_history_seed{seed_index}_all_Ks.csv"),
                    index=False, sep=';', encoding='utf-8'
                )
        except Exception as e:
            print("Error guardando métricas de la semilla:", e)

    # Guardar métricas globales finales
    try:
        if len(all_history_global) > 0:
            df_final = pd.DataFrame(all_history_global)
            df_final.to_csv(
                os.path.join(OUTPUT_ROOT, "metrics_history_all_seeds_Ks.csv"),
                index=False, sep=';', encoding='utf-8'
            )
            print(f"\n{'='*60}")
            print(f"Métricas globales guardadas en:")
            print(f"   {os.path.join(OUTPUT_ROOT, 'metrics_history_all_seeds_Ks.csv')}")
            print(f"{'='*60}")
    except Exception as e:
        print("Error guardando métricas globales finales:", e)

if __name__ == "__main__":
    print("\n" + "="*60)
    print("INICIANDO OPTIMIZACIÓN MOEAD ")
    print("="*60 + "\n")
    ejecutar_todas_las_semillas()
    print("\n" + "="*60)
    print("PROCESO COMPLETADO")
    print("="*60 + "\n")



INICIANDO OPTIMIZACIÓN MOEAD 

Población estimada (combinatoria): 105

=== Semilla 1: 1827841104 ===

------------------------------------------------------------
--- Ejecutando K=10 (semilla 1 → 1827841104) ---
------------------------------------------------------------
n_gen  |  n_eval  | n_nds  |      eps      |   indicator  
     1 |      105 |      4 |             - |             -
     2 |      210 |     70 |  0.3333333333 |         ideal
     3 |      315 |     86 |  0.2500000000 |         ideal
     4 |      420 |     25 |  0.0494846284 |         ideal
     5 |      525 |     45 |  0.2000000000 |         ideal
     6 |      630 |     24 |  0.0933484803 |         nadir
     7 |      735 |     36 |  0.2263681174 |         ideal
     8 |      840 |     43 |  0.0407649582 |         nadir
     9 |      945 |     32 |  0.0866870543 |         ideal
    10 |     1050 |     12 |  0.0642854838 |         nadir
    11 |     1155 |     28 |  0.0317354612 |         ideal
    12 |     1260 